In [ ]:
from vllm import LLM, SamplingParams
import pandas as pd
import numpy as np
import torch.nn.functional as F
import torch
from transformers import AutoTokenizer
from transformers import AutoModelForCausalLM
import re
import os
#os.environ['CUDA_VISIBLE_DEVICES'] = '0,1,2,3'



In [ ]:
llama = LLM(model='hugging-quants/Meta-Llama-3.1-70B-Instruct-AWQ-INT4', tensor_parallel_size = 4, 
            gpu_memory_utilization=0.20,
            download_dir = "../../", max_model_len=5000)

In [ ]:
def ask_about_trials_loosely(patient_summaries, trial_summaries, llama_model):

    tokenizer = llama_model.get_tokenizer()

    prompts = []

    for patient_summary, trial_summary in zip(patient_summaries, trial_summaries):
        messages = [{'role':'system', 'content': """You are a brilliant oncologist with encyclopedic knowledge about cancer and its treatment. 
    Your job is to evaluate whether a given clinical trial is a reasonable consideration for a patient, given a clinical trial summary and a patient summary.\n"""}, 
                {'role':'user', 'content': "Here is a summary of the clinical trial:\n" + trial_summary + "\nHere is a summary of the patient:\n" + patient_summary + """
Base your judgment on whether the patient generally fits the cancer type(s), cancer burden, prior treatment(s), and biomarker criteria specified for the trial.
You do not have to determine if the patient is actually eligible; instead please just evaluate whether it is reasonable for the trial to be considered further by the patient's oncologist.
Some trials have biomarker requirements that are not assessed until formal eligibility screening begins; please ignore these requirements.
Reason step by step, then answer the question "Is this trial a reasonable consideration for this patient?" with a one-word "Yes!" or "No!" answer.
Make sure to include the exclamation point in your final one-word answer."""}]

    
        prompt = tokenizer.apply_chat_template(conversation=messages, add_generation_prompt=True, tokenize=False)
        prompts.append(prompt)
        
    responses = llama_model.generate(
        prompts,     
        SamplingParams(
        temperature=0.0,
        top_p=0.2,
        max_tokens=2048,
        repetition_penalty=1.2,
        stop_token_ids=[tokenizer.eos_token_id, tokenizer.convert_tokens_to_ids("<|eot_id|>")],  # KEYPOINT HERE
    ))

    response_texts = [x.outputs[0].text for x in responses]

    eligibility_results = []

    for response_text in response_texts:
        if ("Yes!" in response_text) or ("YES!" in response_text):
            eligibility_results.append(1.0)
        else:
            eligibility_results.append(0.0)
    
    return responses, response_texts, eligibility_results
    

    



In [ ]:
patient_cohort_candidates = pd.read_csv('top_twenty_patients_tocheck_synthetic_round2.csv')

In [ ]:
patient_cohort_candidates = patient_cohort_candidates.rename(columns={'this_patient':'patient_summary', 'space_summary':'this_space'})

In [ ]:
patient_cohort_candidates.info()

In [ ]:
%%capture
output_list = []
batch_list = []

num_in_batch = 0

for i in range(0, patient_cohort_candidates.shape[0]):
   
    batch_list.append(patient_cohort_candidates.iloc[[i]])
    num_in_batch += 1
    
    if (num_in_batch == 500) or (i == (patient_cohort_candidates.shape[0] - 1)):

        output = pd.concat(batch_list, axis=0)
        _, output['llama_response'], output['eligibility_result'] = ask_about_trials_loosely(output['patient_summary'].tolist(), output['this_space'].astype(str).tolist(), llama)

        output_list.append(output)
        num_in_batch = 0
        batch_list = []
    
    if (len(output_list) > 0 and (i % 500 == 0)) or (i == (patient_cohort_candidates.shape[0] - 1)):
        output_file = pd.concat(output_list, axis=0)
        output_file.to_csv('top_twenty_patients_checked_synthetic_round2.csv')
